In [1]:
"""
This notebook takes the clustering result from the previous notebook, and visualize the clusters,
alongside performing spatial hotspot analysis.
"""

import folium
import geopandas as gpd
import matplotlib.colors
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd

from folium.plugins import MarkerCluster
from shapely.geometry import MultiPoint
from sklearn.cluster import DBSCAN

In [2]:
# Load the experimental data generated from previous notebooks
df_clustered = pd.read_pickle("experimental_data/labeled_merged_data_2022-07-21_to_2025-07-20.pkl")
recent_crime = pd.read_pickle("experimental_data/merged_data_2025-07-18.pkl")

Now that the data has been clustered, I want to make a map to visualize all the hard work and 
analysis done. This will involve three parts:
1. Plotting the clusters from the previous notebook, where I performed UMAP/HDBSCAN clustering.
2. Overlaying recent crimes
3. Performing some hotspot analysis on the clustered data (without cluster labels).

Effectively, I want each to act as a separate layer, and combined, will provide a comprehensive 
analysis of the crime distribution in Philadelphia (at least, up to the date where this data was
collected and clustered). Of course, plotting recent crimes will help let anyone view the spatial
distribution of clusters. Plotting the clusters of crimes will help highlight any particular 
patterns that emerged. But, these patterns may not be statistically significant, so the hotspot
analysis aims to highlight chunks of Philadelphia have statistically significant concentrations of 
crime.

Each of these three layers complement each other. For example, one could see an area as a proper 
hotspot, and then perhaps see two clusters of crime in that hotspot. Finally, recent crimes can help
highlight the most recent observations and confirm the pattern is still active.

The first step is just plotting the recent crimes.

In [3]:
# Extract crime type from the OHE'd columns
crime_type_cols = [col for col in recent_crime.columns if col.startswith('crime_')]
for col in crime_type_cols:
    recent_crime[col] = pd.to_numeric(recent_crime[col], errors='coerce').fillna(0)
# Use idxmax() for a fast, vectorized operation to find the crime type
recent_crime['crime_type'] = recent_crime[crime_type_cols].idxmax(axis=1)

# Define a color map for each crime type
unique_types = recent_crime['crime_type'].unique()
cmap = plt.get_cmap('tab20', len(unique_types))
color_map = {crime: matplotlib.colors.rgb2hex(cmap(i)) for i, crime in enumerate(unique_types)}

# Load Philadelphia boundary GeoJSON
philly_boundary_url = "https://raw.githubusercontent.com/blackmad/neighborhoods/master/philadelphia.geojson"
philly_gdf = gpd.read_file(philly_boundary_url)

# Get the bounding box of Philadelphia to lock the map view
min_lon, min_lat, max_lon, max_lat = philly_gdf.total_bounds
map_bounds = [[min_lat, min_lon], [max_lat, max_lon]]

# Create Folium map of crime, centered at mean lat/lon
m_crime = folium.Map(
    location=[recent_crime['lat'].mean(), recent_crime['lon'].mean()],
    zoom_start=12,
    max_bounds=map_bounds, 
    min_zoom=12
)

# Add the Philadelphia boundary outline to the map
folium.GeoJson(
    philly_gdf[['geometry']], 
    style_function=lambda x: {'color': 'black', 'weight': 2, 'fillOpacity': 0.0},
    name="Philadelphia Boundary"
).add_to(m_crime)

# Create two separate layers for the crime points with new names
# NOTE: This should reflect yesterday's crime in the actual production version
aggregated_view = MarkerCluster(name="Crime Type (Aggregated)").add_to(m_crime)
detailed_view = folium.FeatureGroup(name="Crime Type").add_to(m_crime)

# Add colored markers to both layers
for _, row in recent_crime.iterrows():
    popup_text = row['crime_type'].replace('crime_', '')
    
    # Create a common marker style
    marker_args = {
        "location": [row['lat'], row['lon']],
        "radius": 5,
        "color": color_map[row['crime_type']],
        "fill": True,
        "fill_color": color_map[row['crime_type']],
        "fill_opacity": 0.7,
        "popup": popup_text 
    }
    
    # Add the marker to the aggregated (cluster) view
    folium.CircleMarker(**marker_args).add_to(aggregated_view)
    
    # Add an identical marker to the detailed view
    folium.CircleMarker(**marker_args).add_to(detailed_view)

# Add a layer control button to toggle between the views
folium.LayerControl().add_to(m_crime)

# Add legend for crime type
legend_html_start = '''
     <div style="position: fixed; 
     bottom: 50px; left: 50px; width: 250px; height: 400px; 
     border:2px solid grey; z-index:9999; font-size:14px;
     background-color:white; padding: 10px;">
     <b>Crime Type Legend</b><br>
     <div style="height: 90%; overflow-y: auto;">
     '''
legend_items = ""
for crime_type, color in color_map.items():
    clean_name = crime_type.replace('crime_', '')
    legend_items += f'&nbsp; <i class="fa fa-circle" style="color:{color}"></i> &nbsp; {clean_name}<br>'
legend_html_end = '''
     </div>
     </div>
     '''
full_legend_html = legend_html_start + legend_items + legend_html_end
m_crime.get_root().html.add_child(folium.Element(full_legend_html))

# Save as html
# m_crime.save("layered_crime_map.html")

m_crime

The map above plots the "recent" crimes (again, from the static copy I saved from the first 
notebook), alongside the type. It also has a separate layer for aggregating to make it easier to 
view regions of Philadelphia that have more/less crimes.

Now, I want to add a layer with the clustered crime. This will be based off the clustered labels. 
Note that I could plot every single crime in the clusters, but this would be extremely excessive, as
there would be too many points on the map to be meaningful. It would also decrease the performance 
of the map considerably, so I instead use DBSCAN to effectively create subclusters in each cluster. 
This allows me to make some estimated outlines for areas where lots of crime are clustered densely
together.

In [15]:
# Extract crime type from the OHE'd columns
crime_type_cols = [col for col in recent_crime.columns if col.startswith('crime_')]
for col in crime_type_cols:
    recent_crime[col] = pd.to_numeric(recent_crime[col], errors='coerce').fillna(0)
recent_crime['crime_type'] = recent_crime[crime_type_cols].idxmax(axis=1)

# Define a color map for each crime type
unique_types = recent_crime['crime_type'].unique()
cmap_types = plt.get_cmap('tab20', len(unique_types))
color_map_types = {crime: matplotlib.colors.rgb2hex(cmap_types(i)) for i, crime in enumerate(unique_types)}

# Create a dynamic color map for the clustered crimes
unique_clusters = sorted(df_clustered['cluster_label'].unique())
cmap_clusters = plt.get_cmap('jet', len(unique_clusters))
color_map_clusters = {cluster: matplotlib.colors.rgb2hex(cmap_clusters(i)) for i, cluster in enumerate(unique_clusters)}

# Load Philadelphia boundary GeoJSON
philly_boundary_url = "https://raw.githubusercontent.com/blackmad/neighborhoods/master/philadelphia.geojson"
philly_gdf = gpd.read_file(philly_boundary_url)
min_lon, min_lat, max_lon, max_lat = philly_gdf.total_bounds
map_bounds = [[min_lat, min_lon], [max_lat, max_lon]]

# Create Folium map of crime, centered at mean lat/lon
m_clustered_crime = folium.Map(
    location=[recent_crime['lat'].mean(), recent_crime['lon'].mean()],
    zoom_start=12,
    max_bounds=map_bounds, 
    min_zoom=12
)
# Add the Philadelphia boundary outline to the map
folium.GeoJson(
    philly_gdf[['geometry']], 
    style_function=lambda x: {'color': 'black', 'weight': 2, 'fillOpacity': 0.0},
    name="Philadelphia Boundary"
).add_to(m_clustered_crime)

# Create layers for recent crimes (as circles)
crime_agg_view = MarkerCluster(name="Recent Crimes (Aggregated)").add_to(m_clustered_crime)
crime_det_view = folium.FeatureGroup(name="Recent Crimes (Detailed)").add_to(m_clustered_crime)

# Create new layers for the cluster outlines and icons
cluster_outlines = folium.FeatureGroup(name="Cluster Outlines").add_to(m_clustered_crime)
cluster_icons = folium.FeatureGroup(name="Cluster Icons").add_to(m_clustered_crime)

# Add recent crime markers
for _, row in recent_crime.iterrows():
    popup_text = row['crime_type'].replace('crime_', '')
    marker_args = {
        "location": [row['lat'], row['lon']], "radius": 5,
        "color": color_map_types[row['crime_type']], "fill": True,
        "fill_color": color_map_types[row['crime_type']], "fill_opacity": 0.7,
        "popup": popup_text 
    }
    folium.CircleMarker(**marker_args).add_to(crime_agg_view)
    folium.CircleMarker(**marker_args).add_to(crime_det_view)

# Create subclusters with the clustered data. This is so I can visualize the clusters of crime by
# outlying distinct regions where crimes cluster together, instead of plotting each individuala
# crime which would be a lot harder to view and cause lag on the map when rendering

# Convert df_clustered to a GeoDataFrame and project it for distance calculations
clustered_gdf = gpd.GeoDataFrame(
    df_clustered, 
    geometry=gpd.points_from_xy(df_clustered.lon, df_clustered.lat), 
    crs="EPSG:4326" 
).to_crs("EPSG:2272")

# Group by the primary cluster label to process each cluster
for primary_cluster_label, group in clustered_gdf.groupby('cluster_label'):

    # Extract coordinates for DBSCAN
    coords = np.array(list(zip(group.geometry.x, group.geometry.y)))
    
    # Need at least 3 points to form a hull
    if len(coords) < 3:
        continue

    # Run DBSCAN to find spatial sub-clusters 
    db = DBSCAN(eps=1000, min_samples=3).fit(coords)
    group = group.copy()
    group['sub_cluster'] = db.labels_

    # Now, create an outline for each spatial sub-cluster
    for sub_cluster_label, sub_group in group.groupby('sub_cluster'):
        # Skip noise points from the sub-clustering and groups too small to form a shape
        if sub_cluster_label == -1 or len(sub_group) < 3:
            continue

        # Create a single MultiPoint object from all points in the sub-cluster
        multi_point = MultiPoint(sub_group['geometry'].tolist())
        
        # Calculate the convex hull (the outline)
        hull = multi_point.convex_hull
        
        # Calculate the center for the icon (still in projected CRS)
        centroid_proj = hull.centroid
        
        # Get color and info for this cluster (using the primary label for color)
        icon_color_hex = color_map_clusters.get(primary_cluster_label, '#000000') 
        popup_text = f"Cluster {primary_cluster_label}<br>Sub-Group<br>Count: {len(sub_group)}"

        # Convert hull back to lat/lon for plotting on Folium map
        hull_gdf = gpd.GeoDataFrame([1], geometry=[hull], crs="EPSG:2272").to_crs("EPSG:4326")

        # Add the outline to its layer
        folium.GeoJson(
            hull_gdf.geometry.to_json(),
            style_function=lambda x, color=icon_color_hex: {
                "fillColor": color, "color": color, "weight": 2, "fillOpacity": 0.2,
            }
        ).add_to(cluster_outlines)

        # Convert centroid to lat/lon for the marker
        centroid_gdf = gpd.GeoDataFrame([1], geometry=[centroid_proj], crs="EPSG:2272").to_crs("EPSG:4326")
        centroid_latlon = [centroid_gdf.geometry.y.iloc[0], centroid_gdf.geometry.x.iloc[0]]

        # Define the HTML for the cluster outline icon
        icon_html = f'<div style="text-align: center; color: {icon_color_hex};"><i class="fa fa-tag fa-2x"></i></div>'

        # Add the representative icon to each layer
        folium.Marker(
            location=centroid_latlon,
            icon=folium.DivIcon(
                html=icon_html,
                icon_size=(24, 24),
                icon_anchor=(12, 12)
            ),
            popup=popup_text
        ).add_to(cluster_icons)


# Add a control for controlling the layers
folium.LayerControl().add_to(m_crime)

# Setting up HTML for crime type legend
legend_html_start = '''
     <div style="position: fixed; 
     bottom: 50px; left: 50px; width: 250px; height: 400px; 
     border:2px solid grey; z-index:9998; font-size:14px;
     background-color:white; padding: 10px;">
     <b>Crime Type Legend</b><br>
     <div style="height: 90%; overflow-y: auto;">
     '''
legend_items = ""
for crime_type, color in color_map_types.items():
    clean_name = crime_type.replace('crime_', '')
    legend_items += f'&nbsp; <i class="fa fa-circle" style="color:{color}"></i> &nbsp; {clean_name}<br>'
legend_html_end = '</div></div>'
full_legend_html = legend_html_start + legend_items + legend_html_end
m_clustered_crime.get_root().html.add_child(folium.Element(full_legend_html))

# Setting up HTML for cluster type legend
legend_cluster_html_start = '''
     <div style="position: fixed; 
     bottom: 50px; right: 50px; width: 150px; height: 250px; 
     border:2px solid grey; z-index:9999; font-size:14px;
     background-color:white; padding: 10px;">
     <b>Cluster Legend</b><br>
     <div style="height: 90%; overflow-y: auto;">
     '''
legend_cluster_items = ""
for cluster_label, color in color_map_clusters.items():
    label_text = f"Cluster {cluster_label}" if cluster_label != -1 else "Noise"
    icon_shape = 'tag' if cluster_label != -1 else 'times'
    legend_cluster_items += f'&nbsp; <i class="fa fa-{icon_shape}" style="color:{color}"></i> &nbsp; {label_text}<br>'
legend_cluster_html_end = '</div></div>'
full_legend_cluster_html = legend_cluster_html_start + legend_cluster_items + legend_cluster_html_end
m_clustered_crime.get_root().html.add_child(folium.Element(full_legend_cluster_html))

# Save as html
# m_clustered_crime.save("layered_crime_map.html")

m_clustered_crime

Great! It is now clear that there are some distinct geographical clusters with our data. 
From here, one could see how much of the recent crimes overlap these clusters based on the 
historical data, to see if any crimes would fall into each cluster.

But wait, what does each cluster represent? All that can be viewed now is that crimes are in some
cluster, but there is no information to show what each cluster really represents. So, I make some
minor adjustements to the map to provide some summary statistics for each cluster.

Note that this is a very surface level approach, just to have a basic automated way to label each 
cluster to provide more information. One would ideally want to do more in depth analysis on each
cluster to see if there are any major distinct patterns, especially those that are not picked up by
summary statistics. As such, I do plan to have the option to download individual cluster data in 
the final map, but for now, I will continue with the summary statistics approach.

In [ ]:
# Extract crime type from the OHE'd columns
crime_type_cols = [col for col in recent_crime.columns if col.startswith('crime_')]
for col in crime_type_cols:
    recent_crime[col] = pd.to_numeric(recent_crime[col], errors='coerce').fillna(0)
recent_crime['crime_type'] = recent_crime[crime_type_cols].idxmax(axis=1)

# Define a color map for each crime type
unique_types = recent_crime['crime_type'].unique()
cmap_types = plt.get_cmap('tab20', len(unique_types))
color_map_types = {crime: matplotlib.colors.rgb2hex(cmap_types(i)) for i, crime in enumerate(unique_types)}

# Create a dynamic color map for the clustered crimes
unique_clusters = sorted(df_clustered['cluster_label'].unique())
cmap_clusters = plt.get_cmap('jet', len(unique_clusters))
color_map_clusters = {cluster: matplotlib.colors.rgb2hex(cmap_clusters(i)) for i, cluster in enumerate(unique_clusters)}

# --- NEW: Create a mapping for alphabetical cluster labels ---
# Separate noise points (-1) from actual clusters
cluster_nums = sorted([label for label in unique_clusters if label != -1])
# Create mapping from number to letter (A, B, C...)
alpha_labels = {num: chr(65 + i) for i, num in enumerate(cluster_nums)}
alpha_labels[-1] = 'Noise' # Keep noise label as is
# Apply the new labels to the dataframe
df_clustered['cluster_alpha_label'] = df_clustered['cluster_label'].map(alpha_labels)

# Load Philadelphia boundary GeoJSON
philly_boundary_url = "https://raw.githubusercontent.com/blackmad/neighborhoods/master/philadelphia.geojson"
philly_gdf = gpd.read_file(philly_boundary_url)
min_lon, min_lat, max_lon, max_lat = philly_gdf.total_bounds
map_bounds = [[min_lat, min_lon], [max_lat, max_lon]]

# Create Folium map of crime, centered at mean lat/lon
m_crime = folium.Map(
    location=[recent_crime['lat'].mean(), recent_crime['lon'].mean()],
    zoom_start=12,
    max_bounds=map_bounds, 
    min_zoom=12
)
# Add the Philadelphia boundary outline to the map
folium.GeoJson(
    philly_gdf[['geometry']], 
    style_function=lambda x: {'color': 'black', 'weight': 2, 'fillOpacity': 0.0},
    name="Philadelphia Boundary"
).add_to(m_crime)

# Create layers for recent crimes (as circles)
crime_agg_view = MarkerCluster(name="Recent Crimes (Aggregated)").add_to(m_crime)
crime_det_view = folium.FeatureGroup(name="Recent Crimes (Detailed)").add_to(m_crime)

# Create new layers for the cluster outlines and icons
cluster_outlines = folium.FeatureGroup(name="Cluster Outlines").add_to(m_crime)
cluster_icons = folium.FeatureGroup(name="Cluster Icons").add_to(m_crime)

# Add recent crime markers
for _, row in recent_crime.iterrows():
    popup_text = row['crime_type'].replace('crime_', '')
    marker_args = {
        "location": [row['lat'], row['lon']], "radius": 5,
        "color": color_map_types[row['crime_type']], "fill": True,
        "fill_color": color_map_types[row['crime_type']], "fill_opacity": 0.7,
        "popup": popup_text 
    }
    folium.CircleMarker(**marker_args).add_to(crime_agg_view)
    folium.CircleMarker(**marker_args).add_to(crime_det_view)

# Create subclusters with the clustered data. This is so I can visualize the clusters of crime by
# outlying distinct regions where crimes cluster together, instead of plotting each individuala
# crime which would be a lot harder to view and cause lag on the map when rendering

# Convert df_clustered to a GeoDataFrame and project it for distance calculations
clustered_gdf = gpd.GeoDataFrame(
    df_clustered, 
    geometry=gpd.points_from_xy(df_clustered.lon, df_clustered.lat), 
    crs="EPSG:4326"  # Assume standard lat/lon
).to_crs("EPSG:2272") # Project to a system that uses feet for accurate calculations

# Group by the primary cluster label to process each cluster
for primary_cluster_label, group in clustered_gdf.groupby('cluster_label'):

    # Extract coordinates for DBSCAN
    coords = np.array(list(zip(group.geometry.x, group.geometry.y)))
    
    # Need at least 3 points to form a hull
    if len(coords) < 3:
        continue

    # Run DBSCAN to find spatial sub-clusters 
    db = DBSCAN(eps=1000, min_samples=3).fit(coords)
    group = group.copy()
    group['sub_cluster'] = db.labels_
    
    # Now, create an outline for each spatial sub-cluster
    for sub_cluster_label, sub_group in group.groupby('sub_cluster'):
        # Skip noise points from the sub-clustering and groups too small to form a shape
        if sub_cluster_label == -1 or len(sub_group) < 3:
            continue

        # Create a single MultiPoint object from all points in the sub-cluster
        multi_point = MultiPoint(sub_group['geometry'].tolist())
        
        # Calculate the convex hull (the outline)
        hull = multi_point.convex_hull
        
        # Calculate the center for the icon (still in projected CRS)
        centroid_proj = hull.centroid
        
        # Find the most common crime type in this sub-group
        sub_group_crime_cols = [col for col in sub_group.columns if col.startswith('crime_')]
        # Get the full column name of the most frequent crime
        dominant_crime_col = sub_group[sub_group_crime_cols].sum().idxmax()
        most_common_crime = dominant_crime_col.replace('crime_', '')
        
        # Label the crime if it is extremely dominant or not
        dominant_crime_count = sub_group[dominant_crime_col].sum()
        dominant_crime_pct = dominant_crime_count / len(sub_group)
        dominance_indicator = "✓" if dominant_crime_pct >= 0.5 else "⚠️"
        
        # Calculate average median income, poverty rate, and population density
        avg_median_income = sub_group['income_median'].mean()
        avg_poverty_rate = sub_group['poverty_rate'].mean()
        avg_pop_density = sub_group['pop_density_sq_km'].mean()

        # Get color and info for this cluster (using the primary label for color)
        icon_color_hex = color_map_clusters.get(primary_cluster_label, '#000000')
        
        # Define HTML for detailed popup text with the statistics
        popup_text = f"""
        <b>Cluster {alpha_labels[primary_cluster_label]} (Sub-Group)</b><br>
        Count: {len(sub_group)}<br>
        <hr style='margin: 2px;'>
        <b>Dominant Crime:</b> {most_common_crime} ({dominant_crime_pct:.0%}) {dominance_indicator}<br>
        <b>Avg. Median Income:</b> ${avg_median_income:,.0f}<br>
        <b>Avg. Poverty Rate:</b> {avg_poverty_rate:.1%}<br>
        <b>Avg. Pop. Density:</b> {avg_pop_density:,.0f}/km²
        """

        # Convert hull back to lat/lon for plotting on Folium map
        hull_gdf = gpd.GeoDataFrame([1], geometry=[hull], crs="EPSG:2272").to_crs("EPSG:4326")

        # Add the outline to its layer
        folium.GeoJson(
            hull_gdf.geometry.to_json(), 
            style_function=lambda x, color=icon_color_hex: {
                "fillColor": color, "color": color, "weight": 2, "fillOpacity": 0.2,
            }
        ).add_to(cluster_outlines)

        # Convert centroid to lat/lon for the marker
        centroid_gdf = gpd.GeoDataFrame([1], geometry=[centroid_proj], crs="EPSG:2272").to_crs("EPSG:4326")
        centroid_latlon = [centroid_gdf.geometry.y.iloc[0], centroid_gdf.geometry.x.iloc[0]]

        # Define the HTML for the cluster outline icon
        icon_html = f'<div style="text-align: center; color: {icon_color_hex};"><i class="fa fa-tag fa-2x"></i></div>'

        # Add the representative icon to each layer
        folium.Marker(
            location=centroid_latlon,
            icon=folium.DivIcon(
                html=icon_html,
                icon_size=(24, 24),
                icon_anchor=(12, 12)
            ),
            popup=popup_text
        ).add_to(cluster_icons)


# Add a control for controlling the layers
folium.LayerControl().add_to(m_crime)

# Setting up HTML for crime type legend
legend_html_start = '''
     <div style="position: fixed; 
     bottom: 50px; left: 50px; width: 250px; height: 400px; 
     border:2px solid grey; z-index:9998; font-size:14px;
     background-color:white; padding: 10px;">
     <b>Crime Type Legend</b><br>
     <div style="height: 90%; overflow-y: auto;">
     '''
legend_items = ""
for crime_type, color in color_map_types.items():
    clean_name = crime_type.replace('crime_', '')
    legend_items += f'&nbsp; <i class="fa fa-circle" style="color:{color}"></i> &nbsp; {clean_name}<br>'
legend_html_end = '</div></div>'
full_legend_html = legend_html_start + legend_items + legend_html_end
m_crime.get_root().html.add_child(folium.Element(full_legend_html))

# Setting up HTML for cluster legend
legend_cluster_html_start = '''
     <div style="position: fixed; 
     bottom: 50px; right: 50px; width: 150px; height: 250px; 
     border:2px solid grey; z-index:9999; font-size:14px;
     background-color:white; padding: 10px;">
     <b>Cluster Legend</b><br>
     <div style="height: 90%; overflow-y: auto;">
     '''
legend_cluster_items = ""
for cluster_label, color in color_map_clusters.items():
    label_text = f"Cluster {alpha_labels[cluster_label]}" if cluster_label != -1 else "Noise"
    icon_shape = 'tag' if cluster_label != -1 else 'times'
    legend_cluster_items += f'&nbsp; <i class="fa fa-{icon_shape}" style="color:{color}"></i> &nbsp; {label_text}<br>'
legend_cluster_html_end = '</div></div>'
full_legend_cluster_html = legend_cluster_html_start + legend_cluster_items + legend_cluster_html_end
m_crime.get_root().html.add_child(folium.Element(full_legend_cluster_html))

# Save as html
# m_crime.save("layered_crime_map.html")

m_crime